# NoSQL MongoDB ETL and Query Notebook

In this notebook we will:

- Connect to a MongoDB instance running in Docker.
- Load, validate, and clean patient data from a CSV file into the `patients2` collection.
- Load restaurant data from a JSON file into the `restaurants` collection.
- Run several queries on the imported data.

This end‐to‐end pipeline demonstrates a simple ETL process and data analysis using MongoDB and Python.

## 1. MongoDB Connection

We define a function to connect to MongoDB—with a retry mechanism to ensure that the service is up before we perform any operations.

The connection string is read from the environment (with the default using the container name `medical_mongo`).

In [11]:
import os
import time
import pymongo

def connect_to_mongo():
    """Connects to MongoDB using the URI from environment variables (default uses container name)."""
    mongo_uri = os.getenv("MONGO_URI", "mongodb://localhost:27017/")
    retries = 5
    delay = 5
    
    for attempt in range(retries):
        try:
            client = pymongo.MongoClient(mongo_uri, serverSelectionTimeoutMS=5000)
            client.server_info()  # Force connection test
            print("Connected to MongoDB!")
            return client
        except pymongo.errors.ServerSelectionTimeoutError as e:
            print(f"Attempt {attempt + 1} failed: {e}. Retrying in {delay} seconds...")
            time.sleep(delay)
    
    print("Failed to connect to MongoDB. Exiting.")
    exit(1)

# Connect to MongoDB and get the database
client = connect_to_mongo()
db = client["medical_db"]

print("Database obtained: ", db)

Connected to MongoDB!
Database obtained:  Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True, serverselectiontimeoutms=5000), 'medical_db')


## 2. ETL for Patients Data (CSV)

The CSV file (located in `/app/data` inside the container) contains patient records. In this step we:

- Load the CSV using `pandas`.
- Validate and clean the data (e.g., dropping nulls, parsing dates).
- Insert the data into the `patients2` collection.

In [12]:
import pandas as pd
from datetime import datetime

def parse_date(date_str, format="%d/%m/%Y"):
    """Converts a date string to a Python datetime object."""
    try:
        return datetime.strptime(date_str, format)
    except Exception as e:
        print(f"Date parsing error: {e} for {date_str}")
        return None

def import_patients(db):
    file_path = "data/healthcare_dataset-20250506.csv"
    if not os.path.exists(file_path):
        print("CSV file not found! Check that it exists in the mounted data folder.")
        return
    
    # Load CSV data and drop any rows with null values (you can customize validation as needed)
    df = pd.read_csv(file_path, delimiter=";", encoding="utf-8").dropna()
    
    patient_records = []
    
    # Iterate over each row and build a document for each record
    for _, row in df.iterrows():
        doc = {
            "name": row["Name"],
            "age": int(row["Age"]),
            "gender": row["Gender"],
            "blood_type": row["Blood Type"],
            "medical_condition": row["Medical Condition"],
            "date_of_admission": parse_date(row["Date of Admission"]),
            "doctor": row["Doctor"],
            "hospital": row["Hospital"],
            "insurance_provider": row["Insurance Provider"],
            "billing_amount": float(row["Billing Amount"]),
            "room_number": row["Room Number"],
            "admission_type": row["Admission Type"],
            "discharge_date": parse_date(row["Discharge Date"]),
            "medications": row["Medication"].split(", "),
            "test_results": row["Test Results"]
        }
        patient_records.append(doc)
    
    # Insert records into the 'patients2' collection
    result = db["patients2"].insert_many(patient_records)
    print(f"Inserted {len(result.inserted_ids)} patient records into 'patients2'.")

# Run the import for patients
import_patients(db)

Inserted 55500 patient records into 'patients2'.


## 3. ETL for Restaurants Data (JSON)

Next, we load restaurant data from a JSON file into the `restaurants` collection. In this step we:

- Open and read the JSON file from the mounted data volume.
- Validate that the file exists and contains JSON data.
- Insert the data into MongoDB.

In [13]:
import json

def import_restaurants(db):
    file_path = "data/restaurants.json"
    if not os.path.exists(file_path):
        print("JSON file not found! Check that it exists in the mounted data folder.")
        return
    
    with open(file_path, "r", encoding="utf-8") as jf:
        restaurant_records = json.load(jf)
    
    result = db["restaurants"].insert_many(restaurant_records)
    print(f"Inserted {len(result.inserted_ids)} restaurant records into 'restaurants'.")

# Run the import for restaurants
import_restaurants(db)

Inserted 3772 restaurant records into 'restaurants'.


## 4. Running MongoDB Queries

With the data loaded, we now execute several queries to answer the following questions:

1. **How many patients are in the collection?**
2. **List all patients admitted after January 1, 2023.**
3. **How many patients are older than 50?**
4. **How many patients have the first name "Thomas"?**
5. **Count patients per distinct Medical Condition.**
6. **What is the frequency of usage for each Medication?**
7. **Retrieve all patients currently taking "Lipitor".**

Let's run these queries using PyMongo.

In [14]:
from datetime import datetime

### 1. How many patients are in the collection ?
patient_count = db['patients2'].count_documents({})
print(f"Total patients: {patient_count}")



Total patients: 388500


In [15]:

### 2. List all patients admitted after January 1, 2023
patients_after_date = list(db['patients2'].find({
    "date_of_admission": {"$gt": datetime(2023, 1, 1)}
}))
p = list(db['patients2'].find({"date_of_admission": {"$gt": datetime(2023,1,1)}}))
print(f"Patients admitted after January 1, 2023: {len(patients_after_date)}")
for patient in patients_after_date:
    print(patient["name"], patient["date_of_admission"])

Patients admitted after January 1, 2023: 103936
Bobby JacksOn 2024-01-31 00:00:00
EMILY JOHNSOn 2023-12-20 00:00:00
aaRon MARtiNeZ 2023-08-13 00:00:00
tIMOTHY burNs 2023-06-28 00:00:00
cathy sMaLl 2023-12-23 00:00:00
jOSHUA OLiVer 2023-10-03 00:00:00
WilLIAM cOOPEr 2023-05-18 00:00:00
Erin oRTEga 2023-05-24 00:00:00
kyLE bEnneTT 2023-09-09 00:00:00
mIchael LiU 2024-04-05 00:00:00
TAmARa hErNAndez 2023-08-17 00:00:00
mR. DAVID pIERce Md 2023-11-05 00:00:00
beThaNY MoOrE 2023-04-09 00:00:00
Kim ScOtt 2024-04-07 00:00:00
jOhN hARTmAN 2023-01-07 00:00:00
MicHAEl MillEr 2024-02-06 00:00:00
kEVIn SiMmoNs Jr. 2023-12-28 00:00:00
JONathAn yaTeS 2023-07-24 00:00:00
AdriaN BuckLEY 2023-10-11 00:00:00
tiMOThY myers 2024-03-02 00:00:00
SeaN jenniNGs 2023-11-12 00:00:00
cindY OROzco 2023-05-12 00:00:00
JUan klEiN 2023-08-19 00:00:00
wILLIAM hIlL 2023-05-16 00:00:00
ANNE THOMPSoN 2024-03-24 00:00:00
wilLIAm morTON 2023-06-25 00:00:00
dWAYnE DAViS 2024-01-15 00:00:00
chrisTiNa SChMitt 2023-06-08 00:0

In [16]:
## 3. How many patients are older than 50?
older_than_50 = db['patients2'].count_documents({
    "age": {"$gt": 50}
})
print(f"Patients older than 50: {older_than_50}")


Patients older than 50: 229336


In [17]:

### 4. How many patients have the first name "Thomas"?
# Assuming that the name field may contain full name, you can adjust depending on your naming structure
thomas_count = db['patients2'].count_documents({
    "name": { "$regex": "^Thomas" }
})
print(f"Patients with first name 'Thomas': {thomas_count}")



Patients with first name 'Thomas': 16


In [18]:
### 5. Count patients per distinct Medical Condition
condition_agg = db['patients2'].aggregate([
    {"$group": {"_id": "$medical_condition", "count": {"$sum": 1}}}
])
print("Patient count per Medical Condition:")
for cond in condition_agg:
    print(cond)


Patient count per Medical Condition:
{'_id': 'Cancer', 'count': 73816}
{'_id': 'Obesity', 'count': 73848}
{'_id': 'Diabetes', 'count': 74432}
{'_id': 'Hypertension', 'count': 73960}
{'_id': 'Arthritis', 'count': 74464}
{'_id': 'Asthma', 'count': 73480}


In [19]:
### 6. Frequency of usage for each Medication
med_agg = db['patients2'].aggregate([
    {"$unwind": "$medications"},
    {"$group": {"_id": "$medications", "count": {"$sum": 1}}}
])
print("Medication usage frequency:")
for med in med_agg:
    print(med)

Medication usage frequency:
{'_id': 'Penicillin', 'count': 11068}
{'_id': 'Ibuprofen', 'count': 11127}
{'_id': 'Aspirin', 'count': 11094}
{'_id': 'Lipitor', 'count': 11140}
{'_id': 'Paracetamol', 'count': 11071}


In [20]:
### 7. Retrieve all patients currently taking "Lipitor"
lipitor_patients = list(db['patients2'].find({"medications": "Lipitor"}))
print(f"Patients taking Lipitor: {len(lipitor_patients)}")
for patient in lipitor_patients:
    print(patient["name"], patient["medications"])

Patients taking Lipitor: 11140
aaRon MARtiNeZ ['Lipitor']
rObeRt bAuer ['Lipitor']
ChRISToPHEr BRiGhT ['Lipitor']
KatHRYn StewArt ['Lipitor']
dR. EilEEn thomPsoN ['Lipitor']
mr. KenNEth MoORE ['Lipitor']
NicOlE RodriGUEz ['Lipitor']
DAvID AndErSON ['Lipitor']
NIcOlE LUcErO ['Lipitor']
chRiSTOPHer LEe ['Lipitor']
PeGGY LEe ['Lipitor']
JessIca king ['Lipitor']
jOhN hARTmAN ['Lipitor']
MR. TYler TAYLOR Phd ['Lipitor']
heatHER mIller ['Lipitor']
cathERinE gArDnEr ['Lipitor']
sUZaNnE SchNeIder ['Lipitor']
MIchaEL HUrLEY ['Lipitor']
DR. LaUreN ClaRk DDs ['Lipitor']
JEssicA gUtiERrEz ['Lipitor']
aLaN AlVaREz ['Lipitor']
tiMOthY CoLemaN ['Lipitor']
riTA archER ['Lipitor']
kIm PenA ['Lipitor']
aMAnda lOpeZ ['Lipitor']
LaurA pEtErS ['Lipitor']
EdWARd SMiTh jR. ['Lipitor']
aLliSoN CorDoVA ['Lipitor']
paRkEr moOrE ['Lipitor']
tanya SOto ['Lipitor']
TrACy BUrke ['Lipitor']
jaMEs AnDerSon ['Lipitor']
joshUa rIcHmOnd ['Lipitor']
cyNTHIa HuANG ['Lipitor']
meLiSSA LawRENcE ['Lipitor']
mARY HuNT ['Lipit

## 5. Summary

In this notebook we have:

- Connected to a MongoDB instance running in a Docker container.
- Performed ETL to load patient data from a CSV file and restaurant data from a JSON file.
- Executed several sample MongoDB queries to analyze the data, including counts, date-based filtering, aggregation, and pattern matching.
